In [1]:
import kagglehub
import pandas as pd
import numpy as np
import seaborn as sns
import matplotlib.pyplot as plt

C:\Users\mrsmo\anaconda3\envs\pandas_playground\Lib\site-packages\tqdm\auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


In [2]:

FILE_PATH = r"C:\Users\mrsmo\.cache\kagglehub\datasets\omniamahmoudsaeed\real-estate-sales-2001-2022\versions\1\Real_Estate_Sales_2001-2022_GL.csv"

# Read the CSV
df = pd.read_csv(
    FILE_PATH,
    parse_dates=["Date Recorded"],  # Parse this column as datetime
    low_memory=False                 # Prevent dtype guessing issues on large files
)

# ====================================================
# 4. Convert Columns to Category Type
# ====================================================
cat_columns = ["List Year", "Property Type", "Residential Type", "Town"]
df[cat_columns] = df[cat_columns].astype("category")

# ====================================================
# 5. Clean Up Sales Ratio Column (Remove Known Outliers)
# ====================================================
BAD_SALES_RATIO_INDICES = [
    400223, 387198, 756066, 517857, 950063, 953854, 1076552, 610694, 514136, 395137, 393010, 390655,
    247298, 417869, 474399, 221364, 478279, 251354, 423895, 433617, 863110, 134811, 397613, 479568, 666388, 811579, 413974,
    55055, 270157, 480988, 482770, 271053, 274878, 312695, 353650, 361096, 381148, 384550, 705544, 740634, 750658, 
    466006, 671159, 477350, 457875, 460176, 402630, 339155, 411821, 411133, 91602, 92379, 92547, 92576, 93312, 93480, 93922,
    93958, 94517, 94557, 94807, 95881, 95920, 96250, 98359, 97738, 96673, 96280, 100898, 100500, 98910, 98664, 102937, 101464, 101250, 103665, 
    105660, 108030, 108015, 107930, 107604, 107292, 1096079, 1096037, 1095863, 1089984, 1090576, 1091434, 1092817, 1093416,
    1094013, 1094167, 1097459
]

# Replace bad Sales Ratio values with NaN
df.loc[BAD_SALES_RATIO_INDICES, "Sales Ratio"] = np.nan


pd.set_option("display.max_rows", None)
df.head()


Serial Number List Year Date Recorded     Town          Address  \
0        2020177      2020    2021-04-14  Ansonia    323 BEAVER ST   
1        2020225      2020    2021-05-26  Ansonia   152 JACKSON ST   
2        2020348      2020    2021-09-13  Ansonia  230 WAKELEE AVE   
3        2020090      2020    2020-12-14  Ansonia      57 PLATT ST   
4         210288      2021    2022-06-20     Avon   12 BYRON DRIVE   

   Assessed Value  Sale Amount  Sales Ratio Property Type Residential Type  \
0        133000.0     248400.0       0.5354   Residential    Single Family   
1        110500.0     239900.0       0.4606   Residential     Three Family   
2        150500.0     325000.0       0.4630    Commercial              NaN   
3        127400.0     202500.0       0.6291   Residential       Two Family   
4        179990.0     362500.0       0.4965   Residential            Condo   

  Non Use Code Assessor Remarks OPM remarks  \
0          NaN              NaN         NaN   
1          NaN              NaN         NaN   
2          NaN              NaN         NaN   
3          NaN              NaN         NaN   
4          NaN              NaN         NaN   

                             Location  
0          POINT (-73.06822 41.35014)  
1                                 NaN  
2                                 NaN  
3                                 NaN  
4  POINT (-72.879115982 41.773452988)

In [3]:
#towns that still had sales ratios from 20 and over were excluded because the sales prices
#that cause such disproportionate sales ratios are alost always under $300,000 when people sell partial ownerships
#and it affects the lowest category
#towns_to_exclude = ["Stafford", "East Hartford", "Farmington", "East Haven"]

#df = df[~df["Town"].isin(towns_to_exclude)]

# Drop them from the category list too
#df["Town"] = df["Town"].cat.remove_unused_categories()


In [4]:
#can be used to filter out all low sales 
#df = df[df["Sale Amount"] >= 20_000]


In [5]:
# Define bin edges
df = df[df["Sale Amount"] >= 20_000].copy()
bins = [20_000, 300_000, 700_000, 1_000_000, float("inf")]

# Define bin labels
labels = ["Under $300k", "Mid", "$700k-$1M", "Luxury"]
# Create new column
df["Sale Price Group"] = pd.cut(
    df["Sale Amount"],
    bins=bins,
    labels=labels,
    right=False  # means "less than" on the upper bound
)

# Preview result
df[["Sale Amount", "Sale Price Group"]].head()


Sale Amount Sale Price Group
0     248400.0      Under $300k
1     239900.0      Under $300k
2     325000.0              Mid
3     202500.0      Under $300k
4     362500.0              Mid

In [6]:
df.groupby("Sale Price Group")["Sales Ratio"].mean()


C:\Users\mrsmo\AppData\Local\Temp\ipykernel_6252\1480508669.py:1: FutureWarning: The default of observed=False is deprecated and will be changed to True in a future version of pandas. Pass observed=False to retain current behavior or observed=True to adopt the future default and silence this warning.
  df.groupby("Sale Price Group")["Sales Ratio"].mean()


Sale Price Group
Under $300k    1.318817
Mid            0.730031
$700k-$1M      0.654478
Luxury         0.604502
Name: Sales Ratio, dtype: float64

In [7]:
#town = df.groupby("Town")
#sales_df = town["Sales Ratio"].mean().reset_index()
#sales_df.columns = ["Town", "Avg_Sales_Ratio"]
#sales_df

In [10]:
pd.set_option('display.float_format', '{:,.0f}'.format)


In [14]:
#  Make sure 'Sale Price Group' is categorical
if not pd.api.types.is_categorical_dtype(df["Sale Price Group"]):
    df["Sale Price Group"] = df["Sale Price Group"].astype("category")

#  Add missing categories only if needed
#new_cats = ["<300k", "300k-800k", "800k+"]
#df["Sale Price Group"] = df["Sale Price Group"].cat.add_categories(
 #   [c for c in new_cats if c not in df["Sale Price Group"].cat.categories]
#)

#  Groupby for stats
base_stats = (
    df.groupby(["List Year", "Town"], observed=True)
      .agg(
          Avg_Sale_Amount=("Sale Amount", "mean"),
          Count_Sales=("Sale Price Group", "count"),
          Avg_Sales_Ratio=("Sales Ratio", "mean"),
          Total_Sales=("Sale Amount", "sum")
      )
      .reset_index()
)

#  Count per Sale Price Group
count_per_group = (
    df.groupby(["List Year", "Town", "Sale Price Group"], observed=True)
      .size()
      .reset_index(name="Count_Per_Group")
)

#  Merge together
result = base_stats.merge(count_per_group, on=["List Year", "Town"], how="left")



C:\Users\mrsmo\AppData\Local\Temp\ipykernel_6252\1541102055.py:2: DeprecationWarning: is_categorical_dtype is deprecated and will be removed in a future version. Use isinstance(dtype, pd.CategoricalDtype) instead
  if not pd.api.types.is_categorical_dtype(df["Sale Price Group"]):


In [15]:
result

List Year              Town  Avg_Sale_Amount  Count_Sales  \
0          2001           Ansonia          169,253          354   
1          2001           Ansonia          169,253          354   
2          2001           Ansonia          169,253          354   
3          2001           Ansonia          169,253          354   
4          2001           Ashford          135,294          142   
5          2001           Ashford          135,294          142   
6          2001              Avon          363,807          549   
7          2001              Avon          363,807          549   
8          2001              Avon          363,807          549   
9          2001              Avon          363,807          549   
10         2001       Barkhamsted          162,039           90   
11         2001       Barkhamsted          162,039           90   
12         2001       Barkhamsted          162,039           90   
13         2001            Berlin          207,317          439   
14         2001            Berlin          207,317          439   
15         2001            Berlin          207,317          439   
16         2001            Berlin          207,317          439   
17         2001           Bethany          227,375          151   
18         2001           Bethany          227,375          151   
19         2001           Bethany          227,375          151   
20         2001            Bethel          245,266          504   
21         2001            Bethel          245,266          504   
22         2001            Bethel          245,266          504   
23         2001            Bethel          245,266          504   
24         2001         Bethlehem          201,092           77   
25         2001         Bethlehem          201,092           77   
26         2001         Bethlehem          201,092           77   
27         2001        Bloomfield          240,919          459   
28         2001        Bloomfield          240,919          459   
29         2001        Bloomfield          240,919          459   
30         2001        Bloomfield          240,919          459   
31         2001            Bolton          204,163           93   
32         2001            Bolton          204,163           93   
33         2001            Bozrah          117,478           31   
34         2001          Branford          214,021          777   
35         2001          Branford          214,021          777   
36         2001          Branford          214,021          777   
37         2001          Branford          214,021          777   
38         2001        Bridgeport          141,076         2778   
39         2001        Bridgeport          141,076         2778   
40         2001        Bridgeport          141,076         2778   
41         2001        Bridgeport          141,076         2778   
42         2001       Bridgewater          364,896           49   
43         2001       Bridgewater          364,896           49   
44         2001       Bridgewater          364,896           49   
45         2001       Bridgewater          364,896           49   
46         2001           Bristol          146,274         1479   
47         2001           Bristol          146,274         1479   
48         2001           Bristol          146,274         1479   
49         2001           Bristol          146,274         1479   
50         2001          Brooklyn          159,044          147   
51         2001          Brooklyn          159,044          147   
52         2001          Brooklyn          159,044          147   
53         2001        Burlington          215,745          222   
54         2001        Burlington          215,745          222   
55         2001            Canaan          154,544           32   
56         2001            Canaan          154,544           32   
57         2001            Canaan          154,544           32   
58         2001        Canterbury          132,150   

In [13]:
result.shape

(10774, 8)

In [ ]:
result.to_csv("re_town_levels.csv")

In [ ]:
import os
print(os.getcwd())